In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
import re
import datetime
import time
import pickle
import gc
import warnings
import requests
import gzip
from io import BytesIO

In [2]:
# Limpia la memoria RAM
gc.collect()

0

In [3]:
import pandas as pd

def leer_datos(ruta_archivo):
    # Asegúrate de que la ruta del archivo y el formato sean correctos
    df = pd.read_csv(ruta_archivo, compression='gzip', sep='\t')
    return df

In [4]:


file_url = 'https://storage.googleapis.com/open-courses/austral2023-labo3-d0e5/tb_sellout_01.txt.gz'

# Download the gzipped file using requests
response = requests.get(file_url)

# Check if the request was successful
if response.status_code == 200:
    # Create a file-like object from the response content
    file_content = BytesIO(response.content)

    # Open the gzipped file and read its lines
    with gzip.open(file_content, 'rt', encoding='utf-8') as file:
        lines = file.readlines()
    # Do further processing with the 'lines' variable

else:
    print("Failed to download the file.")


# Extract column names from the first 6 lines (assuming 6 lines for column names)
column_names = [line.strip() for line in lines[:6]]

# Create a dictionary from the data
data = {}
for i, col_name in enumerate(column_names):
    data[col_name] = [line.strip() for line in lines[6 + i::6]]

# Create the DataFrame
df_sellout = pd.DataFrame(data)

stocks = leer_datos('https://storage.googleapis.com/open-courses/austral2023-labo3-d0e5/tb_stocks_02.txt.gz')
master_prod =  pd.read_csv('https://storage.googleapis.com/open-courses/austral2023-labo3-d0e5/tb_productos_02.txt', sep='\t')


In [5]:
df_sellout.head()

periodo customer_id product_id cust_request_qty cust_request_tn       tn
0  201701       10234      20524                2           0.053    0.053
1  201701       10032      20524                1         0.13628  0.13628
2  201701       10217      20524                1         0.03028  0.03028
3  201701       10125      20524                1         0.02271  0.02271
4  201701       10012      20524               11         1.54452  1.54452

In [6]:
# No hay stocks antes del periodo 201810
pd.DataFrame(stocks['periodo'].value_counts()).sort_values(by='periodo', ascending=False)


count
periodo       
201912     925
201911     937
201910     949
201909     929
201908     928
201907     931
201906     914
201905     909
201904     915
201903     893
201902     892
201901     885
201812     891
201811     897
201810     896

In [7]:
# Convertir las columnas a string, int o float antes de hacer el merge
df_sellout['periodo'] = df_sellout['periodo'].astype(int)
df_sellout['product_id'] = df_sellout['product_id'].astype(int)
df_sellout['customer_id'] = df_sellout['customer_id'].astype(int)

df_sellout[['cust_request_qty', 'cust_request_tn','tn']] = df_sellout[['cust_request_qty', 'cust_request_tn','tn']].astype(float)


stocks['periodo'] = stocks['periodo'].astype(int)
stocks['product_id'] = stocks['product_id'].astype(int)
stocks['stock_final']=stocks['stock_final'].astype(float)

master_prod['product_id'] = master_prod['product_id'].astype(int)
master_prod['cat1'] = master_prod['cat1'].astype(str)
master_prod['cat2'] = master_prod['cat2'].astype(str)
master_prod['cat3'] = master_prod['cat3'].astype(str)
master_prod['brand'] = master_prod['brand'].astype(str)


master_prod['sku_size']=master_prod['sku_size'].astype(float)


In [8]:
df_sellout_prod=df_sellout.groupby(['periodo','product_id'])[['cust_request_qty', 'cust_request_tn','tn']].sum().reset_index()

In [9]:
df_sellout_prod_client=df_sellout.groupby(['periodo','customer_id','product_id'])[['cust_request_qty', 'cust_request_tn','tn']].sum().reset_index()

In [10]:
df_sellout_prod=df_sellout_prod.sort_values(by=['product_id','periodo' ])
df_sellout_prod['tn_mas_1']=df_sellout_prod.groupby('product_id')['tn'].shift(-1)
df_sellout_prod['tn_mas_2']=df_sellout_prod.groupby('product_id')['tn'].shift(-2)
df_sellout_prod=df_sellout_prod.reset_index(drop=True)


In [11]:
df_sellout_prod_client=df_sellout_prod_client.sort_values(by=['customer_id','product_id','periodo' ])
df_sellout_prod_client['tn_mas_1']=df_sellout_prod_client.groupby(['customer_id','product_id'])['tn'].shift(-1)
df_sellout_prod_client['tn_mas_2']=df_sellout_prod_client.groupby(['customer_id','product_id'])['tn'].shift(-2)
df_sellout_prod_client=df_sellout_prod_client.reset_index(drop=True)


In [12]:
df_sellout_prod

periodo  product_id  cust_request_qty  cust_request_tn          tn  \
0       201701       20001             479.0        937.72717   934.77222   
1       201702       20001             432.0        833.72187   798.01620   
2       201703       20001             509.0       1330.74697  1303.35771   
3       201704       20001             279.0       1132.94430  1069.96130   
4       201705       20001             701.0       1550.68936  1502.20132   
...        ...         ...               ...              ...         ...   
31238   201701       21295               1.0          0.00699     0.00699   
31239   201708       21296               1.0          0.00651     0.00651   
31240   201701       21297               1.0          0.00579     0.00579   
31241   201708       21298               1.0          0.00573     0.00573   
31242   201708       21299               1.0          0.00546     0.00546   

         tn_mas_1    tn_mas_2  
0       798.01620  1303.35771  
1      1303.35771  1069.96130  
2      1069.96130  1502.20132  
3      1502.20132  1520.06539  
4      1520.06539  1030.67391  
...           ...         ...  
31238         NaN         NaN  
31239         NaN         NaN  
31240         NaN         NaN  
31241         NaN         NaN  
31242         NaN         NaN  

[31243 rows x 7 columns]

In [13]:
df_sellout_prod_client

periodo  customer_id  product_id  cust_request_qty  cust_request_tn  \
0         201701        10001       20001              11.0         99.43861   
1         201702        10001       20001              23.0        198.84365   
2         201703        10001       20001              33.0         92.46537   
3         201704        10001       20001               8.0         13.29728   
4         201705        10001       20001              15.0        101.20711   
...          ...          ...         ...               ...              ...   
2945813   201702        10636       20838               1.0          0.00190   
2945814   201702        10636       20969               1.0          0.00433   
2945815   201702        10636       21178               1.0          0.00197   
2945816   201709        10637       20657               1.0          0.00144   
2945817   201709        10637       20741               1.0          0.00144   

                tn   tn_mas_1   tn_mas_2  
0         99.43861  198.84365   92.46537  
1        198.84365   92.46537   13.29728  
2         92.46537   13.29728  101.00563  
3         13.29728  101.00563  128.04792  
4        101.00563  128.04792  101.20711  
...            ...        ...        ...  
2945813    0.00190        NaN        NaN  
2945814    0.00433        NaN        NaN  
2945815    0.00197        NaN        NaN  
2945816    0.00144        NaN        NaN  
2945817    0.00144        NaN        NaN  

[2945818 rows x 8 columns]

# Vemos que el master tiene duplicados

In [15]:
duplicated_mask = master_prod.duplicated(subset=['product_id'], keep=False)
duplicated_cols = master_prod.loc[duplicated_mask, :]
duplicated_cols


cat1            cat2            cat3     brand  sku_size  product_id
36      HC     ROPA LAVADO           Polvo   LIMPIEX     400.0       20010
37      HC     ROPA LAVADO           Polvo   LIMPIEX     400.0       20010
38      HC     ROPA LAVADO           Polvo   LIMPIEX     800.0       20022
39      HC     ROPA LAVADO           Polvo   LIMPIEX     800.0       20022
41      HC     ROPA LAVADO           Polvo   LIMPIEX     400.0       20021
42      HC     ROPA LAVADO           Polvo   LIMPIEX     400.0       20021
43      HC     ROPA LAVADO           Polvo   LIMPIEX     800.0       20020
44      HC     ROPA LAVADO           Polvo   LIMPIEX     800.0       20020
541  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI       2.0       20278
542  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI       2.0       20278
550  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI       2.0       20192
551  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI       2.0       20192
552  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI      12.0       20037
553  FOODS  SOPAS Y CALDOS      Caldo Cubo     MAGGI      12.0       20037
644  FOODS  SOPAS Y CALDOS      Salsas Wet     MAGGI     350.0       20105
646  FOODS  SOPAS Y CALDOS      Salsas Wet     MAGGI     350.0       20105
898  FOODS        ADEREZOS         Mostaza  MOSTAZA1      60.0       20100
900  FOODS        ADEREZOS         Mostaza  MOSTAZA1      60.0       20100
915     PC         CABELLO  ACONDICIONADOR  SHAMPOO3     350.0       20623
917     PC         CABELLO  ACONDICIONADOR  SHAMPOO3     350.0       20230
981     PC         CABELLO         SHAMPOO  SHAMPOO3     350.0       20623
983     PC         CABELLO         SHAMPOO  SHAMPOO3     350.0       20230

In [16]:
#eliminamos duplicados
master_prod.drop_duplicates(subset=['product_id'], inplace=True)


# Ahora mergeamos la base prod y la prod_customer

In [17]:
# Primero unimos df_sellout_prod con stocks
df_merge1 = pd.merge(df_sellout_prod, stocks, on=['periodo', 'product_id'], how='left')

# Luego unimos el resultado con master_prod
df_final_sellout_prod = pd.merge(df_merge1, master_prod, on='product_id', how='left')

df_final_sellout_prod['cat_1_2']=df_final_sellout_prod['cat1']+'-'+df_final_sellout_prod['cat2']
df_final_sellout_prod['cat_1_2_3']=df_final_sellout_prod['cat1']+'-'+df_final_sellout_prod['cat2']+'-'+df_final_sellout_prod['cat3']
df_final_sellout_prod['cat_1_2_3_brand']=df_final_sellout_prod['cat1']+'-'+df_final_sellout_prod['cat2']+'-'+df_final_sellout_prod['cat3']+'-'+df_final_sellout_prod['brand']

In [18]:
df_final_sellout_prod

periodo  product_id  cust_request_qty  cust_request_tn          tn  \
0       201701       20001             479.0        937.72717   934.77222   
1       201702       20001             432.0        833.72187   798.01620   
2       201703       20001             509.0       1330.74697  1303.35771   
3       201704       20001             279.0       1132.94430  1069.96130   
4       201705       20001             701.0       1550.68936  1502.20132   
...        ...         ...               ...              ...         ...   
31238   201701       21295               1.0          0.00699     0.00699   
31239   201708       21296               1.0          0.00651     0.00651   
31240   201701       21297               1.0          0.00579     0.00579   
31241   201708       21298               1.0          0.00573     0.00573   
31242   201708       21299               1.0          0.00546     0.00546   

         tn_mas_1    tn_mas_2  stock_final cat1         cat2     cat3  brand  \
0       798.01620  1303.35771          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
1      1303.35771  1069.96130          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
2      1069.96130  1502.20132          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
3      1502.20132  1520.06539          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
4      1520.06539  1030.67391          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
...           ...         ...          ...  ...          ...      ...    ...   
31238         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31239         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31240         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31241         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31242         NaN         NaN          NaN  NaN          NaN      NaN    NaN   

       sku_size         cat_1_2               cat_1_2_3  \
0        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
1        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
2        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
3        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
4        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
...         ...             ...                     ...   
31238       NaN             NaN                     NaN   
31239       NaN             NaN                     NaN   
31240       NaN             NaN                     NaN   
31241       NaN             NaN                     NaN   
31242       NaN             NaN                     NaN   

                    cat_1_2_3_brand  
0      HC-ROPA LAVADO-Liquido-ARIEL  
1      HC-ROPA LAVADO-Liquido-ARIEL  
2      HC-ROPA LAVADO-Liquido-ARIEL  
3      HC-ROPA LAVADO-Liquido-ARIEL  
4      HC-ROPA LAVADO-Liquido-ARIEL  
...                             ...  
31238                           NaN  
31239                           NaN  
31240                           NaN  
31241                           NaN  
31242                           NaN  

[31243 rows x 16 columns]

In [19]:
# Primero unimos df_sellout_prod con stocks
df_merge1 = pd.merge(df_sellout_prod_client, stocks, on=['periodo', 'product_id'], how='left')

# Luego unimos el resultado con master_prod
df_final_sellout_prod_client = pd.merge(df_merge1, master_prod, on='product_id', how='left')

df_final_sellout_prod_client['cat_1_2']=df_final_sellout_prod_client['cat1']+'-'+df_final_sellout_prod_client['cat2']
df_final_sellout_prod_client['cat_1_2_3']=df_final_sellout_prod_client['cat1']+'-'+df_final_sellout_prod_client['cat2']+'-'+df_final_sellout_prod_client['cat3']
df_final_sellout_prod_client['cat_1_2_3_brand']=df_final_sellout_prod_client['cat1']+'-'+df_final_sellout_prod_client['cat2']+'-'+df_final_sellout_prod_client['cat3']+'-'+df_final_sellout_prod_client['brand']

In [20]:
#df_test = df_final[(df_final['periodo'] >= 201810) & (df_final['periodo'] <= 201902)]
#df_test=df_test.reset_index(drop=True)


## Hasta aca tenemos dos bases, una que esta anivel de periodo y product_id y una que esta a nivel de periodo, product_id y customer_id.

In [21]:
# Periodo y producto
df_final_sellout_prod

periodo  product_id  cust_request_qty  cust_request_tn          tn  \
0       201701       20001             479.0        937.72717   934.77222   
1       201702       20001             432.0        833.72187   798.01620   
2       201703       20001             509.0       1330.74697  1303.35771   
3       201704       20001             279.0       1132.94430  1069.96130   
4       201705       20001             701.0       1550.68936  1502.20132   
...        ...         ...               ...              ...         ...   
31238   201701       21295               1.0          0.00699     0.00699   
31239   201708       21296               1.0          0.00651     0.00651   
31240   201701       21297               1.0          0.00579     0.00579   
31241   201708       21298               1.0          0.00573     0.00573   
31242   201708       21299               1.0          0.00546     0.00546   

         tn_mas_1    tn_mas_2  stock_final cat1         cat2     cat3  brand  \
0       798.01620  1303.35771          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
1      1303.35771  1069.96130          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
2      1069.96130  1502.20132          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
3      1502.20132  1520.06539          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
4      1520.06539  1030.67391          NaN   HC  ROPA LAVADO  Liquido  ARIEL   
...           ...         ...          ...  ...          ...      ...    ...   
31238         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31239         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31240         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31241         NaN         NaN          NaN  NaN          NaN      NaN    NaN   
31242         NaN         NaN          NaN  NaN          NaN      NaN    NaN   

       sku_size         cat_1_2               cat_1_2_3  \
0        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
1        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
2        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
3        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
4        3000.0  HC-ROPA LAVADO  HC-ROPA LAVADO-Liquido   
...         ...             ...                     ...   
31238       NaN             NaN                     NaN   
31239       NaN             NaN                     NaN   
31240       NaN             NaN                     NaN   
31241       NaN             NaN                     NaN   
31242       NaN             NaN                     NaN   

                    cat_1_2_3_brand  
0      HC-ROPA LAVADO-Liquido-ARIEL  
1      HC-ROPA LAVADO-Liquido-ARIEL  
2      HC-ROPA LAVADO-Liquido-ARIEL  
3      HC-ROPA LAVADO-Liquido-ARIEL  
4      HC-ROPA LAVADO-Liquido-ARIEL  
...                             ...  
31238                           NaN  
31239                           NaN  
31240                           NaN  
31241                           NaN  
31242                           NaN  

[31243 rows x 16 columns]

In [22]:
# Periodo, cliente y producto
df_final_sellout_prod_client

periodo  customer_id  product_id  cust_request_qty  cust_request_tn  \
0         201701        10001       20001              11.0         99.43861   
1         201702        10001       20001              23.0        198.84365   
2         201703        10001       20001              33.0         92.46537   
3         201704        10001       20001               8.0         13.29728   
4         201705        10001       20001              15.0        101.20711   
...          ...          ...         ...               ...              ...   
2945813   201702        10636       20838               1.0          0.00190   
2945814   201702        10636       20969               1.0          0.00433   
2945815   201702        10636       21178               1.0          0.00197   
2945816   201709        10637       20657               1.0          0.00144   
2945817   201709        10637       20741               1.0          0.00144   

                tn   tn_mas_1   tn_mas_2  stock_final cat1         cat2  \
0         99.43861  198.84365   92.46537          NaN   HC  ROPA LAVADO   
1        198.84365   92.46537   13.29728          NaN   HC  ROPA LAVADO   
2         92.46537   13.29728  101.00563          NaN   HC  ROPA LAVADO   
3         13.29728  101.00563  128.04792          NaN   HC  ROPA LAVADO   
4        101.00563  128.04792  101.20711          NaN   HC  ROPA LAVADO   
...            ...        ...        ...          ...  ...          ...   
2945813    0.00190        NaN        NaN          NaN   PC         DEOS   
2945814    0.00433        NaN        NaN          NaN   PC      CABELLO   
2945815    0.00197        NaN        NaN          NaN  NaN          NaN   
2945816    0.00144        NaN        NaN          NaN   HC        HOGAR   
2945817    0.00144        NaN        NaN          NaN   HC        HOGAR   

                    cat3  brand  sku_size         cat_1_2  \
0                Liquido  ARIEL    3000.0  HC-ROPA LAVADO   
1                Liquido  ARIEL    3000.0  HC-ROPA LAVADO   
2                Liquido  ARIEL    3000.0  HC-ROPA LAVADO   
3                Liquido  ARIEL    3000.0  HC-ROPA LAVADO   
4                Liquido  ARIEL    3000.0  HC-ROPA LAVADO   
...                  ...    ...       ...             ...   
2945813             Aero  DEOS2      60.0         PC-DEOS   
2945814  Tratamiento Fem  NIVEA     200.0      PC-CABELLO   
2945815              NaN    NaN       NaN             NaN   
2945816        Repelente    OFF     165.0        HC-HOGAR   
2945817        Repelente    OFF     165.0        HC-HOGAR   

                          cat_1_2_3                   cat_1_2_3_brand  
0            HC-ROPA LAVADO-Liquido      HC-ROPA LAVADO-Liquido-ARIEL  
1            HC-ROPA LAVADO-Liquido      HC-ROPA LAVADO-Liquido-ARIEL  
2            HC-ROPA LAVADO-Liquido      HC-ROPA LAVADO-Liquido-ARIEL  
3            HC-ROPA LAVADO-Liquido      HC-ROPA LAVADO-Liquido-ARIEL  
4            HC-ROPA LAVADO-Liquido      HC-ROPA LAVADO-Liquido-ARIEL  
...                             ...                               ...  
2945813                PC-DEOS-Aero                PC-DEOS-Aero-DEOS2  
2945814  PC-CABELLO-Tratamiento Fem  PC-CABELLO-Tratamiento Fem-NIVEA  
2945815                         NaN                               NaN  
2945816          HC-HOGAR-Repelente            HC-HOGAR-Repelente-OFF  
2945817          HC-HOGAR-Repelente            HC-HOGAR-Repelente-OFF  

[2945818 rows x 17 columns]

# Creamos variable de Producto menor tamaño y mayor tamaño en los que tienen presentaciones similares

### Solo para productos   

In [23]:
prod_presen=df_final_sellout_prod.groupby(['periodo','cat_1_2_3_brand','sku_size'])['tn'].sum().reset_index()
prod_presen=prod_presen.sort_values(by=['cat_1_2_3_brand','periodo' ,'sku_size'])
# Sort the DataFrame by 'periodo' and 'cat_1_2_3_brand'
prod_presen = prod_presen.sort_values(by=['periodo', 'cat_1_2_3_brand'])

# Create a column 'tn_smaller_sku' for the 'tn' value when 'sku_size' is smaller
prod_presen['tn_smaller_sku'] = prod_presen.groupby(['periodo', 'cat_1_2_3_brand'])['tn'].shift(1)

# Create a column 'tn_bigger_sku' for the 'tn' value when 'sku_size' is bigger
prod_presen['tn_bigger_sku'] = prod_presen.groupby(['periodo', 'cat_1_2_3_brand'])['tn'].shift(-1)

# Print the resulting DataFrame

In [24]:
prod_presen

periodo                    cat_1_2_3_brand  sku_size        tn  \
0       201701  FOODS-ADEREZOS-Aji Picante-NATURA     240.0   6.32131   
1       201701     FOODS-ADEREZOS-Barbacoa-NATURA     400.0  11.81983   
2       201701  FOODS-ADEREZOS-Chimichurri-NATURA     350.0   6.03199   
3       201701       FOODS-ADEREZOS-Ketchup-DEOS1     240.0  13.00026   
4       201701      FOODS-ADEREZOS-Ketchup-MAYOS3     240.0  37.69038   
...        ...                                ...       ...       ...   
10835   201912           REF-TE-Especial-TWININGS      10.0   0.01486   
10836   201912           REF-TE-Especial-TWININGS      20.0   0.09684   
10837   201912             REF-TE-Frutas-TWININGS      20.0   0.01188   
10838   201912            REF-TE-Hierbas-TWININGS      20.0   0.07935   
10839   201912              REF-TE-Verde-TWININGS      20.0   0.03422   

       tn_smaller_sku  tn_bigger_sku  
0                 NaN            NaN  
1                 NaN            NaN  
2                 NaN            NaN  
3                 NaN            NaN  
4                 NaN            NaN  
...               ...            ...  
10835             NaN        0.09684  
10836         0.01486            NaN  
10837             NaN            NaN  
10838             NaN            NaN  
10839             NaN            NaN  

[10840 rows x 6 columns]

In [25]:
# Validacion
prod_presen[prod_presen.cat_1_2_3_brand=='REF-TE-Especial-TWININGS']

periodo           cat_1_2_3_brand  sku_size       tn  tn_smaller_sku  \
259     201701  REF-TE-Especial-TWININGS      10.0  0.33812             NaN   
260     201701  REF-TE-Especial-TWININGS      20.0  1.77932         0.33812   
523     201702  REF-TE-Especial-TWININGS      10.0  0.13463             NaN   
524     201702  REF-TE-Especial-TWININGS      20.0  0.84022         0.13463   
786     201703  REF-TE-Especial-TWININGS      10.0  0.47365             NaN   
...        ...                       ...       ...      ...             ...   
10154   201910  REF-TE-Especial-TWININGS      20.0  0.51835         0.09959   
10492   201911  REF-TE-Especial-TWININGS      10.0  0.01311             NaN   
10493   201911  REF-TE-Especial-TWININGS      20.0  0.12160         0.01311   
10835   201912  REF-TE-Especial-TWININGS      10.0  0.01486             NaN   
10836   201912  REF-TE-Especial-TWININGS      20.0  0.09684         0.01486   

       tn_bigger_sku  
259          1.77932  
260              NaN  
523          0.84022  
524              NaN  
786          0.45727  
...              ...  
10154            NaN  
10492        0.12160  
10493            NaN  
10835        0.09684  
10836            NaN  

[72 rows x 6 columns]

### Para productos y clientes 

In [26]:
prod_presen_cust=df_final_sellout_prod_client.groupby(['periodo','customer_id','cat_1_2_3_brand','sku_size'])['tn'].sum().reset_index()
prod_presen_cust=prod_presen_cust.sort_values(by=['cat_1_2_3_brand','periodo' ,'sku_size'])
# Sort the DataFrame by 'periodo' and 'cat_1_2_3_brand'
prod_presen_cust = prod_presen_cust.sort_values(by=['customer_id','periodo', 'cat_1_2_3_brand'])
# Create a column 'tn_smaller_sku' for the 'tn' value when 'sku_size' is smaller
prod_presen_cust['tn_smaller_sku_cust'] = prod_presen_cust.groupby(['customer_id','periodo', 'cat_1_2_3_brand'])['tn'].shift(1)

# Create a column 'tn_bigger_sku' for the 'tn' value when 'sku_size' is bigger
prod_presen_cust['tn_bigger_sku_cust'] = prod_presen_cust.groupby(['customer_id','periodo', 'cat_1_2_3_brand'])['tn'].shift(-1)


In [27]:
prod_presen_cust[~prod_presen_cust.tn_smaller_sku_cust.isna()]

periodo  customer_id                cat_1_2_3_brand  sku_size  \
6        201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     375.0   
7        201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     400.0   
8        201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     500.0   
10       201701        10001  FOODS-ADEREZOS-Mayonesa-DEOS1     340.0   
11       201701        10001  FOODS-ADEREZOS-Mayonesa-DEOS1     475.0   
...         ...          ...                            ...       ...   
33604    201701        10635       PC-DEOS-Pies Talco-DEOS1     200.0   
107113   201703        10635      PC-CABELLO-Styling-GOMINA     280.0   
107115   201703        10635           PC-DEOS-Aero-COLBERT     100.0   
107118   201703        10635             PC-DEOS-Aero-NIVEA     100.0   
107122   201703        10635            PC-DEOS-Talco-DEOS1      90.0   

             tn  tn_smaller_sku_cust  tn_bigger_sku_cust  
6       0.99590             10.92000             3.45946  
7       3.45946              0.99590             0.65520  
8       0.65520              3.45946                 NaN  
10      0.51456              2.81970             2.37667  
11      2.37667              0.51456                 NaN  
...         ...                  ...                 ...  
33604   0.01747              0.01310                 NaN  
107113  0.00153              0.00328                 NaN  
107115  0.00630              0.00392                 NaN  
107118  0.00109              0.00194                 NaN  
107122  0.00111              0.00393                 NaN  

[582052 rows x 7 columns]

In [28]:
# Validacion
prod_presen_cust[(prod_presen_cust.customer_id==10001) & (prod_presen_cust.cat_1_2_3_brand=='FOODS-ADEREZOS-Ketchup-NATURA') ]

periodo  customer_id                cat_1_2_3_brand  sku_size  \
5         201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     240.0   
6         201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     375.0   
7         201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     400.0   
8         201701        10001  FOODS-ADEREZOS-Ketchup-NATURA     500.0   
33614     201702        10001  FOODS-ADEREZOS-Ketchup-NATURA     240.0   
...          ...          ...                            ...       ...   
1243702   201911        10001  FOODS-ADEREZOS-Ketchup-NATURA     400.0   
1243703   201911        10001  FOODS-ADEREZOS-Ketchup-NATURA     500.0   
1277333   201912        10001  FOODS-ADEREZOS-Ketchup-NATURA     240.0   
1277334   201912        10001  FOODS-ADEREZOS-Ketchup-NATURA     250.0   
1277335   201912        10001  FOODS-ADEREZOS-Ketchup-NATURA     500.0   

               tn  tn_smaller_sku_cust  tn_bigger_sku_cust  
5        10.92000                  NaN             0.99590  
6         0.99590             10.92000             3.45946  
7         3.45946              0.99590             0.65520  
8         0.65520              3.45946                 NaN  
33614    20.96640                  NaN             0.66394  
...           ...                  ...                 ...  
1243702   2.20147              1.92465            14.85120  
1243703  14.85120              2.20147                 NaN  
1277333   9.71607                  NaN             0.75075  
1277334   0.75075              9.71607             9.17280  
1277335   9.17280              0.75075                 NaN  

[136 rows x 7 columns]


### Joineamos con las bases totales




In [29]:
df_final_sellout_prod=pd.merge(df_final_sellout_prod, prod_presen[['periodo', 'cat_1_2_3_brand', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku']], on=['periodo', 'cat_1_2_3_brand','sku_size'], how='left')


In [30]:
df_final_sellout_prod_client=pd.merge(df_final_sellout_prod_client, prod_presen[['periodo', 'cat_1_2_3_brand', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku']], on=['periodo', 'cat_1_2_3_brand','sku_size'], how='left')
df_final_sellout_prod_client=pd.merge(df_final_sellout_prod_client, prod_presen_cust[['periodo','customer_id', 'cat_1_2_3_brand', 'sku_size', 'tn_smaller_sku_cust', 'tn_bigger_sku_cust']], on=['periodo','customer_id', 'cat_1_2_3_brand','sku_size'], how='left')


## Aca hacemos por categorias

In [31]:
cat_1=df_final_sellout_prod.groupby(['periodo','cat1'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_tn'})
cat_2=df_final_sellout_prod.groupby(['periodo','cat2'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_2_tn'})
cat_3=df_final_sellout_prod.groupby(['periodo','cat3'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_3_tn'})
brand=df_final_sellout_prod.groupby(['periodo','brand'])['tn'].sum().reset_index().rename(columns={'tn': 'brand_tn'})
cat_1_2=df_final_sellout_prod.groupby(['periodo','cat_1_2'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_tn'})
cat_1_2_3=df_final_sellout_prod.groupby(['periodo','cat_1_2_3'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_3_tn'})
cat_1_2_3_brand=df_final_sellout_prod.groupby(['periodo','cat_1_2_3_brand'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_3_brand_tn'})


In [32]:
df_final_sellout_prod = df_final_sellout_prod.merge(cat_1, on=['periodo', 'cat1'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(cat_2, on=['periodo', 'cat2'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(cat_3, on=['periodo', 'cat3'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(brand, on=['periodo', 'brand'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(cat_1_2, on=['periodo', 'cat_1_2'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(cat_1_2_3, on=['periodo', 'cat_1_2_3'], how='left')
df_final_sellout_prod = df_final_sellout_prod.merge(cat_1_2_3_brand, on=['periodo', 'cat_1_2_3_brand'], how='left')

In [33]:
cat_1_cust=df_final_sellout_prod_client.groupby(['periodo','cat1','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_cust_tn'})
cat_2_cust=df_final_sellout_prod_client.groupby(['periodo','cat2','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_2_cust_tn'})
cat_3_cust=df_final_sellout_prod_client.groupby(['periodo','cat3','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_3_cust_tn'})
brand_cust=df_final_sellout_prod_client.groupby(['periodo','brand','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'brand_cust_tn'})
cat_1_2_cust=df_final_sellout_prod_client.groupby(['periodo','cat_1_2','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_cust_tn'})
cat_1_2_3_cust=df_final_sellout_prod_client.groupby(['periodo','cat_1_2_3','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_3_cust_tn'})
cat_1_2_3_brand_cust=df_final_sellout_prod_client.groupby(['periodo','cat_1_2_3_brand','customer_id'])['tn'].sum().reset_index().rename(columns={'tn': 'cat_1_2_3_brand_cust_tn'})


In [34]:
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_cust, on=['periodo','customer_id', 'cat1'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_2_cust, on=['periodo', 'customer_id','cat2'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_3_cust, on=['periodo', 'customer_id','cat3'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(brand_cust, on=['periodo','customer_id', 'brand'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2_cust, on=['periodo','customer_id', 'cat_1_2'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2_3_cust, on=['periodo','customer_id', 'cat_1_2_3'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2_3_brand_cust, on=['periodo','customer_id', 'cat_1_2_3_brand'], how='left')

In [35]:
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1, on=['periodo', 'cat1'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_2, on=['periodo','cat2'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_3, on=['periodo','cat3'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(brand, on=['periodo', 'brand'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2, on=['periodo', 'cat_1_2'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2_3, on=['periodo', 'cat_1_2_3'], how='left')
df_final_sellout_prod_client = df_final_sellout_prod_client.merge(cat_1_2_3_brand, on=['periodo' ,'cat_1_2_3_brand'], how='left')

In [36]:
df_final_sellout_prod_client


periodo  customer_id  product_id  cust_request_qty  cust_request_tn  \
0         201701        10001       20001              11.0         99.43861   
1         201702        10001       20001              23.0        198.84365   
2         201703        10001       20001              33.0         92.46537   
3         201704        10001       20001               8.0         13.29728   
4         201705        10001       20001              15.0        101.20711   
...          ...          ...         ...               ...              ...   
2945813   201702        10636       20838               1.0          0.00190   
2945814   201702        10636       20969               1.0          0.00433   
2945815   201702        10636       21178               1.0          0.00197   
2945816   201709        10637       20657               1.0          0.00144   
2945817   201709        10637       20741               1.0          0.00144   

                tn   tn_mas_1   tn_mas_2  stock_final cat1  ...  \
0         99.43861  198.84365   92.46537          NaN   HC  ...   
1        198.84365   92.46537   13.29728          NaN   HC  ...   
2         92.46537   13.29728  101.00563          NaN   HC  ...   
3         13.29728  101.00563  128.04792          NaN   HC  ...   
4        101.00563  128.04792  101.20711          NaN   HC  ...   
...            ...        ...        ...          ...  ...  ...   
2945813    0.00190        NaN        NaN          NaN   PC  ...   
2945814    0.00433        NaN        NaN          NaN   PC  ...   
2945815    0.00197        NaN        NaN          NaN  NaN  ...   
2945816    0.00144        NaN        NaN          NaN   HC  ...   
2945817    0.00144        NaN        NaN          NaN   HC  ...   

        cat_1_2_cust_tn cat_1_2_3_cust_tn cat_1_2_3_brand_cust_tn  \
0             987.59783         414.63097               201.08955   
1             915.69477         469.36760               274.20339   
2            1195.71329         503.28711               233.31861   
3             960.45884         371.83138               105.34902   
4            1246.32760         440.08411               149.06781   
...                 ...               ...                     ...   
2945813         0.01029           0.01029                 0.00190   
2945814         0.02379           0.00433                 0.00433   
2945815             NaN               NaN                     NaN   
2945816         0.00288           0.00288                 0.00288   
2945817         0.00288           0.00288                 0.00288   

            cat_1_tn     cat_2_tn    cat_3_tn    brand_tn   cat_1_2_tn  \
0        20304.28696  11153.29607  3871.38669  2655.78679  11153.29607   
1        20183.30152  10799.07240  3908.83266  2213.71985  10799.07240   
2        28883.25590  15565.44487  5403.56525  3500.77761  15565.44487   
3        24453.26459  12470.81761  4242.98976  2855.52603  12470.81761   
4        29339.17333  16396.10155  5520.31852  3992.44834  16396.10155   
...              ...          ...         ...         ...          ...   
2945813   7252.20784   1163.73236   798.38409    28.15389   1163.73236   
2945814   7252.20784   4150.57500    25.10127  1050.65023   4150.57500   
2945815          NaN          NaN         NaN         NaN          NaN   
2945816  29366.04792   3092.61368    49.38107    49.38107   3092.61368   
2945817  29366.04792   3092.61368    49.38107    49.38107   3092.61368   

         cat_1_2_3_tn  cat_1_2_3_brand_tn  
0          3851.59182          1462.91267  
1          3890.19286          1337.53027  
2          5372.68487          2079.30276  
3          4221.64889          1655.68236  
4          5491.49052          2178.40454  
...               ...                 ...  
2945813     798.38409            28.15389  
2945814      25.10127            25.10127  
2945815           NaN                 NaN  
2945816      49.38107            49.38107  
2945817      49.38107            49.38107

## Agregamos de fuentes externas el valor del dolar y la temperatura maxima y minima para buenos aires

In [37]:
dolar=pd.read_csv('dolar_data.csv')
tempe=pd.read_csv('temperatura.csv')


dolar.periodo.astype(int)
tempe.periodo.astype(int)

0     201701
1     201702
2     201703
3     201704
4     201705
5     201706
6     201707
7     201708
8     201709
9     201710
10    201711
11    201712
12    201801
13    201802
14    201803
15    201804
16    201805
17    201806
18    201807
19    201808
20    201809
21    201810
22    201811
23    201812
24    201901
25    201902
26    201903
27    201904
28    201905
29    201906
30    201907
31    201908
32    201909
33    201910
34    201911
35    201912
36    202001
37    202002
38    202003
39    202004
40    202005
41    202006
42    202007
43    202008
44    202009
45    202010
46    202011
47    202012
48    202101
49    202102
50    202103
51    202104
52    202105
53    202106
54    202107
55    202108
56    202109
57    202110
58    202111
59    202112
Name: periodo, dtype: int64

In [38]:
df_final_sellout_prod=pd.merge(df_final_sellout_prod, dolar, on='periodo', how='left')
df_final_sellout_prod_client=pd.merge(df_final_sellout_prod_client, dolar, on='periodo', how='left')

In [39]:
df_final_sellout_prod=pd.merge(df_final_sellout_prod, tempe, on='periodo', how='left')
df_final_sellout_prod_client=pd.merge(df_final_sellout_prod_client, tempe, on='periodo', how='left')

# Empezamos con el FE temporal 

## Considerando solo Product_id y periodo

El código proporcionado define una función llamada create_lagged_features que se utiliza para crear características de retraso, estadísticas móviles, características de tendencia y características de estacionariedad en un DataFrame de pandas. Estas características son útiles para modelar series temporales y otros tipos de datos secuenciales.

La función toma cuatro parámetros: df que es el DataFrame de entrada, lag_periods que es una lista de los períodos de retraso a considerar, window_sizes que es una lista de los tamaños de ventana para las estadísticas móviles, y feature_names que es una lista de los nombres de las características para las que se crearán las nuevas características.

Primero, la función ordena el DataFrame por 'product_id' y 'periodo'. Luego, para cada nombre de característica en feature_names, para cada tamaño de ventana en window_sizes, y para cada período de retraso en lag_periods, la función crea una nueva característica de retraso. Esto se hace utilizando el método shift de pandas, que desplaza los datos hacia abajo en un número especificado de filas (el período de retraso).

Después, para cada nombre de característica y cada tamaño de ventana, la función crea tres nuevas características: una media móvil, una desviación estándar móvil y una característica de tendencia. La media móvil y la desviación estándar móvil se calculan utilizando el método rolling de pandas, que proporciona una ventana móvil de los datos. La característica de tendencia se calcula utilizando el método diff de pandas, que calcula la diferencia entre filas consecutivas.

Finalmente, la función crea características de estacionariedad adicionales utilizando más características de retraso (hasta 24 períodos). Estas características se crean de la misma manera que las características de retraso anteriores.

La función devuelve el DataFrame con las características añadidas.

In [42]:
import pandas as pd

def create_lagged_features(df, lag_periods, window_sizes, feature_names):
    """
    Create lagged features, rolling statistics, trend features, and stationarity features for the specified feature names.

    Parameters:
    df (pd.DataFrame): The input DataFrame.
    lag_periods (list): A list of lag periods to consider.
    window_sizes (list): A list of window sizes for rolling statistics.
    feature_names (list): A list of feature names to create features for.

    Returns:
    pd.DataFrame: A DataFrame with the added features.
    """
    df = df.sort_values(by=['product_id', 'periodo'])

    for feature_name in feature_names:
        for window_size in window_sizes:
            for lag in lag_periods:
                df[f'{feature_name}_lag_{lag}_win_{window_size}'] = df.groupby('product_id')[feature_name].shift(lag)

            df[f'{feature_name}_rolling_mean_win_{window_size}'] = df.groupby('product_id')[feature_name].rolling(window=window_size).mean().reset_index(level=0, drop=True)
            df[f'{feature_name}_rolling_std_win_{window_size}'] = df.groupby('product_id')[feature_name].rolling(window=window_size).std().reset_index(level=0, drop=True)
            df[f'{feature_name}_trend_win_{window_size}'] = df.groupby('product_id')[feature_name].diff()

            # Capture stationarity using additional lag features (up to 24 periods)
            for i in range(1, 25):
                df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby('product_id')[feature_name].shift(i)

    return df




In [43]:
df_final_sellout_prod.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 31243 entries, 0 to 31242
Data columns (total 29 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   periodo             31243 non-null  int64  
 1   product_id          31243 non-null  int64  
 2   cust_request_qty    31243 non-null  float64
 3   cust_request_tn     31243 non-null  float64
 4   tn                  31243 non-null  float64
 5   tn_mas_1            30010 non-null  float64
 6   tn_mas_2            28797 non-null  float64
 7   stock_final         13691 non-null  float64
 8   cat1                31014 non-null  object 
 9   cat2                31014 non-null  object 
 10  cat3                31014 non-null  object 
 11  brand               31014 non-null  object 
 12  sku_size            31014 non-null  float64
 13  cat_1_2             31014 non-null  object 
 14  cat_1_2_3           31014 non-null  object 
 15  cat_1_2_3_brand     31014 non-null  object 
 16  tn_s

In [44]:
numeric_cols = df_final_sellout_prod.select_dtypes(include='float').columns.tolist()
print(numeric_cols)
numeric_cols=['cust_request_qty', 'cust_request_tn', 'tn', 'stock_final', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku', 'usd_blue_max', 'usd_oficial_max', 'temp_max', 'temp_min', 'cat_1_tn', 'cat_2_tn', 'cat_3_tn', 'brand_tn', 'cat_1_2_tn', 'cat_1_2_3_tn', 'cat_1_2_3_brand_tn']


['cust_request_qty', 'cust_request_tn', 'tn', 'tn_mas_1', 'tn_mas_2', 'stock_final', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku', 'cat_1_tn', 'cat_2_tn', 'cat_3_tn', 'brand_tn', 'cat_1_2_tn', 'cat_1_2_3_tn', 'cat_1_2_3_brand_tn', 'usd_blue_max', 'usd_oficial_max', 'temp_max', 'temp_min']


In [45]:

# Example usage:
lag_periods = range(1, 25)  # Consider lags from 1 to 24 periods
window_sizes = range(1, 13)  # Consider window sizes from 1 to 12
feature_names = numeric_cols  # Add feature names you want to process

# Create lagged features, rolling statistics, trends, and stationarity features for the specified features
df_final_sellout_prod_fe = create_lagged_features(df_final_sellout_prod, lag_periods, window_sizes, feature_names)

# Select the features you want for your model
#selected_features = [col for col in df.columns if any(feat in col for feat in feature_names)]

# Now you can use the df DataFrame for training your model with the selected features

/var/folders/5_/gws729vx0pn71fdvj09_cqghn9zl4w/T/ipykernel_74771/3389885854.py:29: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby('product_id')[feature_name].shift(i)
/var/folders/5_/gws729vx0pn71fdvj09_cqghn9zl4w/T/ipykernel_74771/3389885854.py:29: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby('product_id')[feature_name].shift(i)
/var/folders/5_/gws729vx0pn71fdvj09_cqghn9zl4w/T/ipyke

In [ ]:

# Assuming your DataFrame is called df
na_counts = df_final_sellout_prod_fe.isna().sum()
print(na_counts)


In [47]:
df_final_sellout_prod_fe.to_parquet('df_final_sellout_prod_fe.parquet', index=False)


## Considerando product_id, customer_id y periodo

El código proporcionado define una función llamada create_lagged_features_cst que se utiliza para crear características de retraso, estadísticas móviles, características de tendencia y características de estacionariedad en un DataFrame de pandas. Estas características son útiles para modelar series temporales y otros tipos de datos secuenciales.

La función toma cuatro parámetros: df que es el DataFrame de entrada, lag_periods que es una lista de los períodos de retraso a considerar, window_sizes que es una lista de los tamaños de ventana para las estadísticas móviles, y feature_names que es una lista de los nombres de las características para las que se crearán las nuevas características.

Primero, la función ordena el DataFrame por 'product_id' y 'periodo'. Luego, para cada nombre de característica en feature_names, para cada tamaño de ventana en window_sizes, y para cada período de retraso en lag_periods, la función crea una nueva característica de retraso. Esto se hace utilizando el método shift de pandas, que desplaza los datos hacia abajo en un número especificado de filas (el período de retraso).

Después, para cada nombre de característica y cada tamaño de ventana, la función crea tres nuevas características: una media móvil, una desviación estándar móvil y una característica de tendencia. La media móvil y la desviación estándar móvil se calculan utilizando el método rolling de pandas, que proporciona una ventana móvil de los datos. La característica de tendencia se calcula utilizando el método diff de pandas, que calcula la diferencia entre filas consecutivas.

Finalmente, la función crea características de estacionariedad adicionales utilizando más características de retraso (hasta 24 períodos). Estas características se crean de la misma manera que las características de retraso anteriores.

La función devuelve el DataFrame con las características añadidas.

In [311]:
def create_lagged_features_cst(df, lag_periods, window_sizes, feature_names):
    """
    Create lagged features, rolling statistics, trend features, and stationarity features for the specified feature names.

    Parameters:
    df (pd.DataFrame): The input DataFrame.
    lag_periods (list): A list of lag periods to consider.
    window_sizes (list): A list of window sizes for rolling statistics.
    feature_names (list): A list of feature names to create features for.

    Returns:
    pd.DataFrame: A DataFrame with the added features.
    """
    df = df.sort_values(by=['product_id', 'customer_id', 'periodo'])

    for feature_name in feature_names:
        for window_size in window_sizes:
            for lag in lag_periods:
                df[f'{feature_name}_lag_{lag}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(lag)
            
            # Reset the index after groupby and shift
            df.reset_index(drop=True, inplace=True)

        df[f'{feature_name}_rolling_mean_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).mean().reset_index(level=0, drop=True)
        df[f'{feature_name}_rolling_std_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).std().reset_index(level=0, drop=True)
        df[f'{feature_name}_trend_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].diff()
        
        # Reset the index after groupby and rolling
        df.reset_index(drop=True, inplace=True)

        # Capture stationarity using additional lag features (up to 24 periods)
        for i in range(1, 25):
            df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(i)
        
        # Reset the index after groupby and shift
        df.reset_index(drop=True, inplace=True)

    return df

In [50]:
numeric_cols = df_final_sellout_prod_client.select_dtypes(include='float').columns.tolist()
print(numeric_cols)

['cust_request_qty', 'cust_request_tn', 'tn', 'tn_mas_1', 'tn_mas_2', 'stock_final', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku', 'tn_smaller_sku_cust', 'tn_bigger_sku_cust', 'cat_1_cust_tn', 'cat_2_cust_tn', 'cat_3_cust_tn', 'brand_cust_tn', 'cat_1_2_cust_tn', 'cat_1_2_3_cust_tn', 'cat_1_2_3_brand_cust_tn', 'cat_1_tn', 'cat_2_tn', 'cat_3_tn', 'brand_tn', 'cat_1_2_tn', 'cat_1_2_3_tn', 'cat_1_2_3_brand_tn', 'usd_blue_max', 'usd_oficial_max', 'temp_max', 'temp_min']


In [313]:
df_final_sellout_prod_client

periodo  customer_id  product_id  cust_request_qty  cust_request_tn  \
0         201701        10001       20001              11.0         99.43861   
1         201702        10001       20001              23.0        198.84365   
2         201703        10001       20001              33.0         92.46537   
3         201704        10001       20001               8.0         13.29728   
4         201705        10001       20001              15.0        101.20711   
...          ...          ...         ...               ...              ...   
2945813   201702        10636       20838               1.0          0.00190   
2945814   201702        10636       20969               1.0          0.00433   
2945815   201702        10636       21178               1.0          0.00197   
2945816   201709        10637       20657               1.0          0.00144   
2945817   201709        10637       20741               1.0          0.00144   

                tn   tn_mas_1   tn_mas_2  stock_final cat1  ...  \
0         99.43861  198.84365   92.46537          NaN   HC  ...   
1        198.84365   92.46537   13.29728          NaN   HC  ...   
2         92.46537   13.29728  101.00563          NaN   HC  ...   
3         13.29728  101.00563  128.04792          NaN   HC  ...   
4        101.00563  128.04792  101.20711          NaN   HC  ...   
...            ...        ...        ...          ...  ...  ...   
2945813    0.00190        NaN        NaN          NaN   PC  ...   
2945814    0.00433        NaN        NaN          NaN   PC  ...   
2945815    0.00197        NaN        NaN          NaN  NaN  ...   
2945816    0.00144        NaN        NaN          NaN   HC  ...   
2945817    0.00144        NaN        NaN          NaN   HC  ...   

        usd_oficial_max temp_max temp_min  cat_1_cust_tn cat_2_cust_tn  \
0                 16.38     30.4     20.9     1661.17133     987.59783   
1                 16.12     30.1     20.6     2134.19490     915.69477   
2                 15.94     26.9     18.0     2302.90434    1195.71329   
3                 15.78     23.5     14.3     2432.95105     960.45884   
4                 16.41     19.5     12.3     2632.32210    1246.32760   
...                 ...      ...      ...            ...           ...   
2945813           16.12     30.1     20.6        0.03408       0.01029   
2945814           16.12     30.1     20.6        0.03408       0.02379   
2945815           16.12     30.1     20.6            NaN           NaN   
2945816           17.87     20.3     11.6        0.00288       0.00288   
2945817           17.87     20.3     11.6        0.00288       0.00288   

        cat_3_cust_tn brand_cust_tn  cat_1_2_cust_tn  cat_1_2_3_cust_tn  \
0           417.78172     393.84493        987.59783          414.63097   
1           471.77079     402.36215        915.69477          469.36760   
2           505.95851     375.73642       1195.71329          503.28711   
3           375.63393     232.99436        960.45884          371.83138   
4           442.27133     455.29737       1246.32760          440.08411   
...               ...           ...              ...                ...   
2945813       0.01029       0.00190          0.01029            0.01029   
2945814       0.00433       0.00433          0.02379            0.00433   
2945815           NaN           NaN              NaN                NaN   
2945816       0.00288       0.00288          0.00288            0.00288   
2945817       0.00288       0.00288          0.00288            0.00288   

         cat_1_2_3_brand_cust_tn  
0                      201.08955  
1                      274.20339  
2                      233.31861  
3                      105.34902  
4                      149.06781  
...                          ...  
2945813                  0.00190  
2945814                  0.00433  
2945815                      NaN  
2945816                  0.00288  
2945817                  0.00288  

[2945818 rows x 32 columns]

In [316]:
def create_lagged_features_cst(df, lag_periods, window_sizes, feature_names):
    df = df.sort_values(by=['product_id', 'customer_id', 'periodo'])

    for feature_name in feature_names:
        for window_size in window_sizes:
            for lag in lag_periods:
                new_column_name = f'{feature_name}_lag_{lag}_win_{window_size}'
                df[new_column_name] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(lag)

        # Reset the index after groupby and shift
        df.reset_index(drop=True, inplace=True)

        # Add rolling statistics columns
        df[f'{feature_name}_rolling_mean_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).mean().reset_index(level=0, drop=True)
        df[f'{feature_name}_rolling_std_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).std().reset_index(level=0, drop=True)
        df[f'{feature_name}_trend_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].diff()

        # Reset the index after groupby and rolling
        df.reset_index(drop=True, inplace=True)

        # Capture stationarity using additional lag features (up to 24 periods)
        for i in range(1, 25):
            df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(i)

        # Reset the index after groupby and shift
        df.reset_index(drop=True, inplace=True)

    return df



In [40]:
def create_lagged_features_cst(df, lag_periods, window_sizes, feature_names):
    df = df.sort_values(by=['product_id', 'customer_id', 'periodo'])

    for feature_name in feature_names:
        for window_size in window_sizes:
            for lag in lag_periods:
                df[f'{feature_name}_lag_{lag}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(lag).reset_index(drop=True)

            df[f'{feature_name}_rolling_mean_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).mean().reset_index(drop=True)
            df[f'{feature_name}_rolling_std_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].rolling(window=window_size).std().reset_index(drop=True)
            df[f'{feature_name}_trend_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].diff().reset_index(drop=True)

            for i in range(1, 25):
                df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(i).reset_index(drop=True)

    return df

In [41]:
# Example usage:
lag_periods = range(1, 12)  # Consider lags from 1 to 24 periods
window_sizes = range(1, 13)  # Consider window sizes from 1 to 12
feature_names = ['cust_request_qty', 'cust_request_tn', 'tn', 'stock_final', 'sku_size', 'tn_smaller_sku', 'tn_bigger_sku', 'tn_smaller_sku_cust', 'tn_bigger_sku_cust', 'cat_1_cust_tn', 'cat_2_cust_tn', 'cat_3_cust_tn', 'brand_cust_tn', 'cat_1_2_cust_tn', 'cat_1_2_3_cust_tn', 'cat_1_2_3_brand_cust_tn', 'cat_1_tn', 'cat_2_tn', 'cat_3_tn', 'brand_tn', 'cat_1_2_tn', 'cat_1_2_3_tn', 'cat_1_2_3_brand_tn', 'usd_blue_max', 'usd_oficial_max', 'temp_max', 'temp_min']  # Add feature names you want to process

# Create lagged features, rolling statistics, trends, and stationarity features for the specified features
df_final_sellout_prod_client_fe = create_lagged_features_cst(df_final_sellout_prod_client, lag_periods, window_sizes, feature_names)

# Select the features you want for your model
#selected_features = [col for col in df.columns if any(feat in col for feat in feature_names)]

# Now you can use the df DataFrame for training your model with the selected features


/var/folders/5_/gws729vx0pn71fdvj09_cqghn9zl4w/T/ipykernel_82460/3773222675.py:14: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(i).reset_index(drop=True)
/var/folders/5_/gws729vx0pn71fdvj09_cqghn9zl4w/T/ipykernel_82460/3773222675.py:14: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[f'{feature_name}_stationarity_lag_{i}_win_{window_size}'] = df.groupby(['product_id', 'customer_id'])[feature_name].shift(

In [1]:
df_final_sellout_prod_client_fe.head(10)

NameError: name 'df_final_sellout_prod_client_fe' is not defined